### Preprocessing Eclipse Bug reports

#### Description of attributes
    Size of data: (103805, 13)
    Bug ID: Unique Identifier
    Important attributes: Product, Component, Assignee, Summary, Changed (possibly the frequency it has been changed with difference between opened and changed), Summary, Severity, Priority:
    Unimportant attributes: Status and Resolution. [We will not know them for the test samples]
    
    Summary has 103802 values i.e. 3 missing values will have to investigate them.


### Fixing of data formatting in the csv
    Some rows have shifted right by a few columns due the the data delimiting in the csv like rows 3613, 258
    That has been fixed and a new file total_fixed.csv has been saved

In [1]:
import pandas as pd

In [2]:
df = pd.read_csv('../data/total.csv')

In [6]:
df.shape

(103805, 13)

In [17]:
import numpy as np

In [19]:
len(np.unique(df['Bug ID']))

103805

In [5]:
df.drop('Bug ID',axis=1,inplace=False).describe()

Product Component                  Assignee    Status Resolution  \
count     103805    103805                    103805    103805     103805   
unique         4        27                       307         6          7   
top     Platform        UI  jdt-ui-inbox@eclipse.org  RESOLVED      FIXED   
freq       60644     37694                      3668     75695      53211   

       Summary       Changed Priority Severity     Keywords Summary.1  \
count   103802        103805   103805   103805         6814    103802   
unique  102339         88794        5        7          106    102339   
top     #NAME?  9/27/05 9:12       P3   normal  performance    #NAME?   
freq        37           759    88902    71546         1272        37   

                Opened  
count           103805  
unique           96130  
top     10/10/01 23:05  
freq                61

In [10]:
df.loc[df.Summary.isnull(),:]

Bug ID   Product Component                        Assignee    Status  \
538      1719       JDT     Debug         darin.eclipse@gmail.com    CLOSED   
26852   38524  Platform       SWT  platform-swt-inbox@eclipse.org    CLOSED   
44151   65246       JDT        UI         dirk_baeumer@ch.ibm.com  VERIFIED   

      Resolution Summary        Changed Priority Severity Keywords Summary.1  \
538      INVALID     NaN   11/2/01 8:56       P3   normal      NaN       NaN   
26852    INVALID     NaN   6/5/03 13:04       P3   normal      NaN       NaN   
44151      FIXED     NaN  6/11/04 10:41       P3   normal      NaN       NaN   

               Opened  
538    10/10/01 22:18  
26852    6/5/03 11:35  
44151     6/2/04 5:39

In [13]:
df.iloc[[257,258],:]

Bug ID   Product Component                   Assignee    Status  \
3610    5706       JDT      Core  philippe_mulet@fr.ibm.com  RESOLVED   
3611    8230  Platform     Debug    darin.eclipse@gmail.com  VERIFIED   

      Resolution                                            Summary  \
3610  WORKSFORME  Cannot add two folders w/ same name but diff p...   
3611       FIXED  Console does not show process as <terminated>;...   

          Changed Priority Severity Keywords  \
3610  2/7/02 8:46       P1   normal      NaN   
3611  2/7/02 9:14       P3   normal      NaN   

                                              Summary.1         Opened  
3610  Cannot add two folders w/ same name but diff p...   11/9/01 8:59  
3611  Console does not show process as <terminated>;...  1/23/02 14:09

In [14]:
df.to_csv('../data/total_fixed.csv',index=False,header=True)

### Text preprocessing according to the Paper

1. Tokenization - word level
2. Stop-Word removal - 30 stop words: TIFIDF has that feature
3. Stemming - Porter Stemming.

This will be done only on the Summary attribute as others are categorical attributes.


In [2]:
import pandas as pd
import numpy as np

In [3]:
df = pd.read_csv('../data/total_fixed.csv')

In [4]:
df.drop(['Keywords','Summary.1','Status','Resolution','Changed','Opened'],axis=1,inplace=True)

In [5]:
df.columns

Index([u'Bug ID', u'Product', u'Component', u'Assignee', u'Summary',
       u'Priority', u'Severity'],
      dtype='object')

In [8]:
df.dropna(inplace=True)

In [7]:
df.isnull().sum()

Bug ID       0
Product      0
Component    0
Assignee     0
Summary      3
Priority     0
Severity     0
dtype: int64

In [ ]:
df.reset_index(inplace=True)

### Null values removed and only important features are kept

In [13]:
from nltk.tokenize import RegexpTokenizer
from nltk.stem.porter import PorterStemmer
import re

tokenizer = RegexpTokenizer(r'\w+')
stopwords = set(nltk.corpus.stopwords.words('english'))
stemmer = PorterStemmer()

In [129]:
# tokenizer.tokenize('Eighty-seven miles to go, yet.  Onward!')
def tokenize_stop_stem(text):
    try:
        tokens = tokenizer.tokenize(text)
        # filter out any tokens not containing letters (e.g., numeric tokens, raw punctuation) and stem
        filtered_tokens = []
        for token in tokens:
            token = token.lower()
            if token not in stopwords:
                if not re.search('[0-9]', token):
                    try:
                        token = stemmer.stem(token)
                        filtered_tokens.append(token)
                    except UnicodeDecodeError:
                        print 'illeagal token ignored:',token
                        pass
    except UnicodeDecodeError:
        print 'illeagal token ignored:',token
        pass
    return filtered_tokens

### Run sklearn countvectorizer

In [15]:
from sklearn.feature_extraction.text import CountVectorizer

In [128]:
countVect = CountVectorizer(input='content',lowercase=False, max_features=395996, tokenizer=tokenize_stop_stem, decode_error='ignore')

In [20]:
countVector = countVect.fit_transform(df.Summary)

tokenizing Task Smoke Tests (1GHE30L)
tokenizing Preferences Smoke Tests (1GIIP94)
tokenizing Navigator Smoke Tests (1GHDUB4)
tokenizing Outline Smoke Tests (1GHFYSV)
tokenizing Properties View Smoke Tests (1GHFYQ0)
tokenizing Welcome Editor Smoke Tests (1GHFZ5B)
tokenizing Text Editor Smoke Tests (1GHFZ95)
tokenizing Import Wizard Smoke Tests (1GI3ZW4)
tokenizing Export Wizard Smoke Tests (1GI5JX0)
tokenizing Properties Dialog Smoke Tests (1GIIPDQ)
tokenizing Walkback in classloader on J9 (1GIEN3W)
tokenizing type hiearchy: need a short cut to toggle from sub to supertypes (1G4CM8Z)
tokenizing Can select folder outside project as bin output (1G5Y99R)
tokenizing No editor preferences (1GBPMBT)
tokenizing internal error in refactoring wizard (1GL4LRF)
tokenizing JAR Packager dialog to small if opened directly from .jardesc (1GL2WCM)
tokenizing SWTException from CompletionProposalPopup (1GLDGUI)
tokenizing Deletion of packages fails (1GKZK3V)
tokenizing organize imports - 'not parsed' er

tokenizing Null Pointer Exception when delete 2 projects with the search view open (1GI7GCW)
tokenizing Path Extension in Classpath Variable Selection dialog does not remember intermediate folders (1GIEUG1)
tokenizing JAR Packager: Fix trailing spaces workaround in seal label (1GIFZKR)
tokenizing Reconciling: Problems with the C parser (1GIHV3E)
tokenizing Erroneous reference to xerces in StandardDocletPageBuffer (1GIWXZS)
tokenizing Refactoring: Should not use computed strings (1GIWKFJ)
tokenizing NL: No NLS support for Java keywords "public", "protected" etc. in dialogs  (1GIYQKG)
tokenizing Search page extension point doc inaccurate (1GJ6EXO)
tokenizing [UI] Unzoom can cause view to move tab folder (1GFOGFE)
tokenizing [UI] Finish button still grayed out even though file name is pasted  (1GGYVYG)
tokenizing [UI] Dragging view border near scroll bar detaches view (1GHDIIU)
tokenizing Editor Selection Dialog: UI suggestions (1GI6RPE)
tokenizing TaskListMarker violates API (1GL2XHA)
to

tokenizing No revealing in type hierarchy when "show members in hierarchy"
tokenizing Printing single page prints entire document
tokenizing Internal JDI error
tokenizing VMDisconnectedException notification on resume
tokenizing SWT: StyledText does not switch colour (1GILHIW)
tokenizing Avoid references to preference pages
tokenizing plugin import should handle multiple versions of a plugin
tokenizing Format should keep position
tokenizing Three entries for 'Parser' in all types list
tokenizing New Class button in empty workspace should be more supportive
tokenizing incorrect bracket matching
tokenizing Source Lookup API Change (1GDIS1I)
tokenizing Build Path Page - entering a path in the selection box is ignored (1GEPA6S)
tokenizing TVT: Hover help for "Keep else if on the same line" is incorrect (backwards)
tokenizing "Keep else if on the same line" appears to do the reverse
tokenizing Java formatter preferences for "else if" sample is backwards
tokenizing Code formatter preference 

tokenizing can't start ... get SIGSEV11
tokenizing Editor tab error tick missing on open
tokenizing Auto created javadoc comments start with /*
tokenizing Rename of <Foo>Plugin.java crashes
tokenizing Two Java Doc hovers
tokenizing BIDI: Keyboard Input Layer in Java Class name field
tokenizing NPE out of new page book view
tokenizing Perps ext. to add new view fails because of folders.
tokenizing [JFace] TableViewer: MapElement problem (1GITISX)
tokenizing History View - Drag + Drop
tokenizing History View - "Add to workspace" required
tokenizing GP closing Eclipse
tokenizing FileViewer example does not have drag and drop
tokenizing First editor tab missing close button (1GF7QIQ)
tokenizing Getting remote contents of an empty file fails
tokenizing Getting remote contents fails on file obtained from ILogEntry
tokenizing Names in File menu document history could be shortened
tokenizing find dialog box obscures result
tokenizing Contributing sub-menu with items still does not work
tokeniz

tokenizing 'refactor' menu missing from the type hierarchy perspective
tokenizing CodeAssist - results should be sorted alphabetically (1FW31TZ)
tokenizing Why is the <clinit> method included in the outliner? (1FW8PBX)
tokenizing EC: Find/replace gets stuck in infinite loop (1GLCBZE)
tokenizing Open a type is extremely slow
tokenizing support navigation package fragment -> packages views (1FWL3KF)
tokenizing Replace with local history in content outline throws error
tokenizing "MyCorporation" copyright in jdt.ui
tokenizing New class wizard should assume inner class when activated on class (1G2NQAH)
tokenizing Type hierarchy:
tokenizing DCR: open package to hierarchy (1G8Q7UL)
tokenizing Move Class - Busy cursor visible only at the beginning (1G45S0N)
tokenizing NewJavaProjectWizard - enabled 'un/check all' buttons for an empty list (1G46XJO)
tokenizing Need keyboard shortcuts to navigate between document windows
tokenizing Move Destination shows empty folders as packages (1G46Z2X)
toke

...

tokenizing Template and doc unclear when refering to the product file
tokenizing Don't re-parse target platform extensions if workspace cache not saved
tokenizing Default value of configs in build.properties should default to the current os/ws/arch
tokenizing Extensions Registry Notifications ver.2
tokenizing [Forms] Behaviour of Section with fixed style changed between Eclipse 3.0 and 3.1 (and later)
tokenizing [Webapp] Navigation buttons always enabled
tokenizing Initial launch of help system does not have disabled forward and back buttons
tokenizing [call hierarchy] should allow searches for fields
tokenizing [misc] Adopt new IME support - was: SquigglesStrategy draws on top of IME text
tokenizing [JUnit] label decorations for succeeded/failed tests
tokenizing Import PSF should honor "Always run in background" workspace setting
tokenizing [Sync View] The Startup and Workspace pages in the Sync view preferences dialog are missing help
tokenizing [call hierarchy] Call hierarchy should

tokenizing Compare viewer does not draw background colors for changes (StyledText)
tokenizing Creating a button clears mnemonics
tokenizing Exception in Mozilla browser code not caught, leads to crash
tokenizing UNDERLINE_ERROR text style does not work for IME strings
tokenizing Adherent TextStyles must be continuous
tokenizing underline text style needs clarification
tokenizing Mnemonics should not turn on until ALT is pressed
tokenizing GTK-BIDI: RTL support in CoolBar.
tokenizing Typing return in Spinner enters space
tokenizing GTK-BIDI: RTL support in ColorDialog
tokenizing GTK-BIDI: RTL support in FontDialog
tokenizing GTK-BIDI: RTL support in DirectoryDialog.
tokenizing GTK-BIDI: RTL support in FileDialog.
tokenizing GTK-BIDI: RTL support in MessageBox
tokenizing GTK-BIDI: RTL support in ScrollBar.
tokenizing getItemCount() incorrect in Vista for VIRTUAL trees
tokenizing Target editor's content tab buttons disappear completely
tokenizing XOR mode doesn't work with GC
tokenizing S

tokenizing [leopard] crash when finishing any snippet
tokenizing check out problems for platform-ui
tokenizing [launcher] RCP product export for solaris motif sparc executable missing
tokenizing Eclipse crashes on MacOSX Leopard
tokenizing [prov] Get rid of IResolvedInstallableUnit and IResolvedInstallableUnitFragment
tokenizing [prov] - API cleanup - IInstallableUnitConstants
tokenizing [Vista x64] Graphical Issues
tokenizing EventManager swallows Throwable
tokenizing bundle resolution support for p2 provisioned SDK
tokenizing Need a way to spec "Resource-Only" EE
tokenizing [rulers] Selecting line does not include carriage return
tokenizing JDT .java Editor Matching Escaped Parenthesis issue
tokenizing org.eclipse.jdt.ui.postsavelistener.cleanup  AssertionFailedException
tokenizing [rename] Reinstate the rename dialog
tokenizing Launch ANT script outside from the eclipse Workspace
tokenizing copy from outline view
tokenizing Event loop exception in Synchronizer.runAsyncMessages
token

tokenizing typing semicolon should append semicolon at end of line
tokenizing [override method] Allow Override/Implement of inherited interfaces
tokenizing Migrate from deprecated key bindings API
tokenizing White list for Step Filtering
tokenizing renaming launch configs does not remove original
tokenizing making local config shared creates "non-existant dup" in LCD
tokenizing [View Mgmt] Please bring back floating/detached views
tokenizing [Forms] FormText::getSelectedLinkHref() returns an Object instead of a String
tokenizing Linux JVM 1.5 & 1.6 crash when print button is pressed
tokenizing [Forms] FormEditor.commitPages() throws ClassCastException
tokenizing Incorrect casting statement in FormEditor.commitPages(boolean)
tokenizing [Forms] Adopt new MPE key binding API
tokenizing Scary stack trace in log when authorization infrastructure is missing
tokenizing Tree fails to register double-click while tool tip visible
tokenizing Table#getItem(Point) inconsitent on OSX when used witho

tokenizing [Markers] New markers view shows two breakpoint entries when none set
tokenizing Add decoration for optional plug-ins
tokenizing [Markers] Markers are using the category icon when flat
tokenizing [GlobalActions] [IDE] Allow to extend RefreshAction
tokenizing [spy] could turn the "contributing plugin" section into a link to plugin manifest
tokenizing [search] References to annotations not found in class file without source
tokenizing [registryview] Show Only Disabled Plug-ins / Disabled Icon
tokenizing [Commands] org.eclipse.ui.commandImages API and documentation error
tokenizing [Markers] All content provider needs a type field
tokenizing [Markers] Tasks content has mark completed enabled for non editable tasks
tokenizing [spy] provide 'Copy Qualified Name' for hyperlinked classes
tokenizing [Metadata] update version number of org.eclipse.ui.ide
tokenizing [content assist] 'for' templates have higher rank in content assist then for keyword
tokenizing [Markers] New Markers vi

In [21]:
countVector

<103802x18087 sparse matrix of type '<type 'numpy.int64'>'
	with 592582 stored elements in Compressed Sparse Row format>

In [22]:
countVector.shape

(103802, 18087)

### Summary attribute has been preprocessed. Get dummy variables and join them as CSR and join with countvectors

In [25]:
dummy_df = pd.get_dummies( df[['Product','Component','Assignee','Severity']] )

In [130]:
dummy_df.head()

Product_Equinox  Product_JDT  Product_PDE  Product_Platform  Component_APT  \
0                0            0            0                 1              0   
1                0            0            0                 1              0   
2                0            0            0                 1              0   
3                0            0            0                 1              0   
4                0            0            0                 1              0   

   Component_Ant  Component_Build  Component_CVS  Component_Compare  \
0              0                0              0                  0   
1              0                0              0                  0   
2              0                0              0                  0   
3              0                0              0                  0   
4              0                0              0                  0   

   Component_Compendium        ...         Assignee_wtp-dev@eclipse.org  \
0                     0        ...                                    0   
1                     0        ...                                    0   
2                     0        ...                                    0   
3                     0        ...                                    0   
4                     0        ...                                    0   

   Assignee_ymnk@jcraft.com  Assignee_zhiyongl@ca.ibm.com  Severity_blocker  \
0                         0                             0                 0   
1                         0                             0                 0   
2                         0                             0                 0   
3                         0                             0                 0   
4                         0                             0                 0   

   Severity_critical  Severity_enhancement  Severity_major  Severity_minor  \
0                  0                     0               0               0   
1                  0                     0               0               0   
2                  0                     0               0               0   
3                  0                     0               0               0   
4                  0                     0               0               0   

   Severity_normal  Severity_trivial  
0                1                 0  
1                1                 0  
2                1                 0  
3                1                 0  
4                1                 0  

[5 rows x 345 columns]

In [80]:
from scipy import sparse

In [82]:
dummy_sparse = sparse.csr_matrix(dummy_df.values)

In [92]:
inputDF = sparse.hstack((dummy_sparse,countVector),format="csr")

In [98]:
print inputDF[0]

  (0, 3)	1
  (0, 26)	1
  (0, 49)	1
  (0, 343)	1
  (0, 15202)	1
  (0, 16170)	1
  (0, 16265)	1


In [100]:
print countVector[0]

  (0, 14857)	1
  (0, 15825)	1
  (0, 15920)	1


In [99]:
print dummy_sparse[0]

  (0, 3)	1
  (0, 26)	1
  (0, 49)	1
  (0, 343)	1


### Input Data is ready for algorithms to process

##### Random Forest with training accuracy

In [ ]:
from sklearn.ensemble import RandomForestClassifier

In [101]:
rfr.fit(inputDF,df['Priority'])

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=10, n_jobs=-1,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False)

In [103]:
rfr.score(inputDF,df['Priority'])

0.9884298953777384

In [113]:
print rfr.score(inputDF[list(df.loc[df.Priority=='P1',:].index)], df['Priority'].loc[df.Priority=='P1'] )
print rfr.score(inputDF[list(df.loc[df.Priority=='P2',:].index)], df['Priority'].loc[df.Priority=='P2'] )
print rfr.score(inputDF[list(df.loc[df.Priority=='P3',:].index)], df['Priority'].loc[df.Priority=='P3'] )
print rfr.score(inputDF[list(df.loc[df.Priority=='P4',:].index)], df['Priority'].loc[df.Priority=='P4'] )
print rfr.score(inputDF[list(df.loc[df.Priority=='P5',:].index)], df['Priority'].loc[df.Priority=='P5'] )

0.942521631644
0.942525739606
0.999426315257
0.870751154008
0.866542520174


## Cross validation on the dataset with F1-Score (our evaluation metric)

In [132]:
from sklearn.cross_validation import cross_val_score
from sklearn.metrics import make_scorer
from sklearn.metrics import f1_score

In [119]:
f1scorer = make_scorer(f1_score, average='macro')

In [120]:
f1scorer

make_scorer(f1_score, average=macro)

In [121]:
cvscores = cross_val_score(rfr, inputDF, df['Priority'],scoring=f1scorer ,cv=3,n_jobs=-1, )

In [122]:
cvscores

array([ 0.23816111,  0.24208552,  0.23872431])

In [125]:
cvscores_acc = cross_val_score(rfr, inputDF, df['Priority'],scoring='accuracy', cv=10, n_jobs=-1)

In [127]:
np.mean(cvscores_acc),np.std(cvscores_acc)

(0.83135657064570512, 0.043975080942427851)